In [3]:
!pip install openai


In [51]:
from openai import OpenAI
client = OpenAI()

## llm 分析

In [1]:
# 读入数据
import pandas
df = pandas.read_csv('news.csv', index_col=0)
df

标题                 时间       来源  \
0           AI创作新风潮：影视业，拥抱AI新机遇  2023年08月28日 04:03  人民日报海外版   
1   雨中跪地救人的“二次元小姐姐” 是位喜欢动漫的苏州医生  2023年07月26日 02:23     扬子晚报   
2         首批AI克隆明星上线，不只是娱乐业“躺赚”  2023年06月05日 01:40      新京报   
3             “10后”的流行密语你能对上几个？  2023年06月01日 09:51     羊城晚报   
4  （经济观察）虚拟数字人“现身”各行各业 释放可观商业价值  2023年05月20日 09:37    中国新闻网   
5       网络热梗也能成为热门IP IP如何吸引Z世代？  2022年12月15日 01:00    北京青年报   
6        玩具市场迎来多元需求 成年人“入坑”潮流玩具  2022年10月26日 15:31    北京青年报   
7          越来越多场景应用 “数字人”走进大众生活  2022年09月07日 19:55    中国新闻网   
8       爱的是“皮”还是“魂”？虚拟偶像凭什么“圈粉”  2022年09月07日 19:55    中国新闻网   
9       唱歌跳舞的“皮套人”？这个千亿级生意没那么简单  2022年09月07日 19:55    中国新闻网   

                                                  正文  
0  前不久，一部以元宇宙为概念的国潮微短剧《神女杂货铺》在某视频平台播出，讲述了一个现代女孩穿越...  
1  7月21日，在上海某漫展场馆外，一名年轻男子突然在雨中晕厥倒地，这一幕，恰好被一位穿cosp...  
2  现实中偶像与粉丝互动被AI复制到虚拟空间中，虚实边界被进一步打破。\n花30元就可以和网红明...  
3  羊城晚报记者 秦小杰\n作为互联网新生代，“10后”的小学生有哪些流行“密语”？喜欢什么样的...  
4  中新社上海5月20日电 (谢梦圆)近期，多个品牌启用虚拟形象作为代言人、社交平台AI博主大受...  
5  随着网络文化的发展，新时代IP内容也随之扩展创新，不仅涵盖动漫、影视、游戏、潮玩，甚至一个符...  
6  一年一度的双11来临，潮流玩具市场再度成为各大电商平台必争之地，玩具市场迎来更多元的市场需求...  
7  中新网北京9月7日电 (中新财经 吴家驹)从“初音未来”到“洛天依”再到“嘉然”，近年来，“...  
8  虚拟偶像深受当下年轻人的欢迎。艾媒咨询调研显示，中国虚拟人爱好者中，19岁至30岁之间的年轻...  
9  近日，一条微博热搜将人们的视线拉回到了虚拟偶像的身上，一名来自美国的虚拟主播在短短两小时内吸...

In [13]:
for index, row in df.iterrows():
    completion = client.chat.completions.create(
        model="gpt-4o-mini",
        temperature=0,
        messages=[
            {"role": "system", "content": "你是一个新闻标题判定器，你要分析我提供新闻标题是否属于'标题党'。你只能回答是或否"},
            {
                "role": "user",
                "content": f"标题：{row.标题}"
            }
        ]
    )
    
    print(completion.choices[0].message.content, row.标题)

否 AI创作新风潮：影视业，拥抱AI新机遇
是 雨中跪地救人的“二次元小姐姐” 是位喜欢动漫的苏州医生
是 首批AI克隆明星上线，不只是娱乐业“躺赚”
是 “10后”的流行密语你能对上几个？
否 （经济观察）虚拟数字人“现身”各行各业 释放可观商业价值
否 网络热梗也能成为热门IP IP如何吸引Z世代？
否 玩具市场迎来多元需求 成年人“入坑”潮流玩具
否 越来越多场景应用 “数字人”走进大众生活
是 爱的是“皮”还是“魂”？虚拟偶像凭什么“圈粉”
是 唱歌跳舞的“皮套人”？这个千亿级生意没那么简单


## 情感分析

In [55]:
response = client.embeddings.create(
    input=['情感标签：积极', '情感标签：消极'],
    model="text-embedding-3-small"
)
positive = response.data[0].embedding
negative = response.data[1].embedding

In [56]:
import numpy as np

def cosine_similarity(vec1, vec2):
    """
    计算两个向量之间的余弦相似度。

    参数:
    vec1 -- 第一个向量，列表或numpy数组
    vec2 -- 第二个向量，列表或numpy数组

    返回:
    余弦相似度，介于-1和1之间
    """
    # 将输入转换为numpy数组
    vec1 = np.array(vec1)
    vec2 = np.array(vec2)
    
    # 计算向量的点积
    dot_product = np.dot(vec1, vec2)
    
    # 计算向量的范数（模）
    norm_vec1 = np.linalg.norm(vec1)
    norm_vec2 = np.linalg.norm(vec2)
    
    # 计算余弦相似度
    if norm_vec1 == 0 or norm_vec2 == 0:
        return 0.0  # 如果其中一个向量是零向量，则相似度为0
    else:
        return dot_product / (norm_vec1 * norm_vec2)

# 示例用法
similarity = cosine_similarity(positive, negative)
print(f"余弦相似度: {similarity}")

余弦相似度: 0.7307260589905838


In [58]:
# 载入数据
import pandas
df = pandas.read_csv('news.csv', index_col = 0)
df

标题                 时间       来源  \
0           AI创作新风潮：影视业，拥抱AI新机遇  2023年08月28日 04:03  人民日报海外版   
1   雨中跪地救人的“二次元小姐姐” 是位喜欢动漫的苏州医生  2023年07月26日 02:23     扬子晚报   
2         首批AI克隆明星上线，不只是娱乐业“躺赚”  2023年06月05日 01:40      新京报   
3             “10后”的流行密语你能对上几个？  2023年06月01日 09:51     羊城晚报   
4  （经济观察）虚拟数字人“现身”各行各业 释放可观商业价值  2023年05月20日 09:37    中国新闻网   
5       网络热梗也能成为热门IP IP如何吸引Z世代？  2022年12月15日 01:00    北京青年报   
6        玩具市场迎来多元需求 成年人“入坑”潮流玩具  2022年10月26日 15:31    北京青年报   
7          越来越多场景应用 “数字人”走进大众生活  2022年09月07日 19:55    中国新闻网   
8       爱的是“皮”还是“魂”？虚拟偶像凭什么“圈粉”  2022年09月07日 19:55    中国新闻网   
9       唱歌跳舞的“皮套人”？这个千亿级生意没那么简单  2022年09月07日 19:55    中国新闻网   

                                                  正文  
0  前不久，一部以元宇宙为概念的国潮微短剧《神女杂货铺》在某视频平台播出，讲述了一个现代女孩穿越...  
1  7月21日，在上海某漫展场馆外，一名年轻男子突然在雨中晕厥倒地，这一幕，恰好被一位穿cosp...  
2  现实中偶像与粉丝互动被AI复制到虚拟空间中，虚实边界被进一步打破。\n花30元就可以和网红明...  
3  羊城晚报记者 秦小杰\n作为互联网新生代，“10后”的小学生有哪些流行“密语”？喜欢什么样的...  
4  中新社上海5月20日电 (谢梦圆)近期，多个品牌启用虚拟形象作为代言人、社交平台AI博主大受...  
5  随着网络文化的发展，新时代IP内容也随之扩展创新，不仅涵盖动漫、影视、游戏、潮玩，甚至一个符...  
6  一年一度的双11来临，潮流玩具市场再度成为各大电商平台必争之地，玩具市场迎来更多元的市场需求...  
7  中新网北京9月7日电 (中新财经 吴家驹)从“初音未来”到“洛天依”再到“嘉然”，近年来，“...  
8  虚拟偶像深受当下年轻人的欢迎。艾媒咨询调研显示，中国虚拟人爱好者中，19岁至30岁之间的年轻...  
9  近日，一条微博热搜将人们的视线拉回到了虚拟偶像的身上，一名来自美国的虚拟主播在短短两小时内吸...

In [72]:
response = client.embeddings.create(
    input=df.标题 ,
    model="text-embedding-3-small"
)
embeddings = [i.embedding for i in response.data]


In [73]:
sentiment = []
for title, emb in zip(df.标题, embeddings):
    if cosine_similarity(emb, positive) > cosine_similarity(emb, negative):
        result = 'positive'
    else:
        result = 'negative'
    print(result, title)
    sentiment.append(result)
sentiment

positive AI创作新风潮：影视业，拥抱AI新机遇
positive 雨中跪地救人的“二次元小姐姐” 是位喜欢动漫的苏州医生
positive 首批AI克隆明星上线，不只是娱乐业“躺赚”
negative “10后”的流行密语你能对上几个？
positive （经济观察）虚拟数字人“现身”各行各业 释放可观商业价值
positive 网络热梗也能成为热门IP IP如何吸引Z世代？
positive 玩具市场迎来多元需求 成年人“入坑”潮流玩具
positive 越来越多场景应用 “数字人”走进大众生活
positive 爱的是“皮”还是“魂”？虚拟偶像凭什么“圈粉”
positive 唱歌跳舞的“皮套人”？这个千亿级生意没那么简单


['positive',
 'positive',
 'positive',
 'negative',
 'positive',
 'positive',
 'positive',
 'positive',
 'positive',
 'positive']

## 聚类

In [39]:
# 读入数据
df = pandas.read_csv('souhu.csv', index_col=0)
df

时间                                           标题  \
0   2024-09-28 23:34:43                               MMD初音未来，UNDEAD   
1   2024-09-06 15:57:15                                     初音未来17周年   
2   2024-10-23 21:41:45                          MMD初音未来五人组，Unveiled   
3   2024-09-25 20:18:35                                 MMD初音未来，单色骑士   
4   2024-08-10 14:30:53                                 MMD初音未来，SHOW   
..                  ...                                          ...   
70  2024-09-01 10:29:15  初音未来大折扣！PSN港服《ProjectDIVAFTDX》5折优惠，音游迷怎能错过？   
71  2024-10-08 19:10:47               无视一切的恋爱，宅男当年曾娶初音未来领结婚证，如今怎么样了？   
72  2024-07-30 15:19:15               《世界计划：破碎的世界与不能唱歌的未来》官宣制作初音未来主演   
73  2024-09-22 19:56:47              还记得和初音未来结婚的男子吗？一年过去了，他们的现状怎么样了？   
74  2024-09-02 08:39:04     神っぽいな(像神一样呐)|初音ミク(初音未来)|揉揉酱自制小提琴谱|五线谱|乐谱   

                                           URL  \
0   https://www.sohu.com/a/812565548_120122317   
1      https://www.sohu.com/a/806861635_532686   
2   https://www.sohu.com/a/819573079_120122317   
3   https://www.sohu.com/a/811660644_120122317   
4   https://www.sohu.com/a/799888119_120122317   
..                                         ...   
70     https://www.sohu.com/a/805408718_362225   
71  https://www.sohu.com/a/814623848_121166535   
72     https://www.sohu.com/a/797235003_211762   
73  https://www.sohu.com/a/810770579_121166539   
74  https://www.sohu.com/a/805585736_120879343   

                                                   摘要  
0                                      MMD初音未来，UNDEAD  
1       角色名：初音未来CN：安凉公主殿下生日快乐wwෆ(˶''ᵕ''˶)ෆ图片授权来源：次元岛…  
2                                 MMD初音未来五人组，Unveiled  
3                                        MMD初音未来，单色骑士  
4                                        MMD初音未来，SHOW  
..                                                ...  
70  《初音未来ProjectDIVAFutureToneDX》不仅是一款音乐游戏，更是一次全面的...  
71  在日本，一男子却做出更加惊人之举，因为他的爱情已经跨越了种族、肤色甚至是虚实，和一位虚拟人物...  
72  初音未来主演的剧场版动画《世界计划：破碎的世界与不能唱歌的未来》现已正式开始制作，并且预告和...  
73  现在社会，科技已经深入到生活每一个细节，大到国家重量级项目，小到家中一个小小的扫地机器人，不...  
74  这首歌曲是二次元音乐人匹诺曹P的《神芽na(像神一样呐)》，歌词讽刺现代社会中对“神性”的盲...  

[75 rows x 4 columns]

In [40]:
response = client.embeddings.create(
    input=df.标题,
    model="text-embedding-3-small"
)

In [33]:
!pip install scikit-learn

In [43]:
embeddings = [i.embedding for i in response.data]
import numpy as np
from sklearn.cluster import KMeans

# 假设你有一个嵌入的列表或数组
# 这里我们用随机数据来模拟嵌入
# 每个嵌入是一个长度为128的向量
np.random.seed(42)  # 为了结果可重复

# 定义聚类的数量
num_clusters =10

# 创建KMeans模型
kmeans = KMeans(n_clusters=num_clusters, random_state=42)

# 训练模型
kmeans.fit(embeddings)

# 获取每个嵌入的聚类标签
labels = kmeans.labels_

# 输出结果
print("聚类标签：", labels)

聚类标签： [2 3 1 2 2 2 2 2 2 2 2 1 2 2 5 2 3 2 6 2 2 2 7 4 2 3 4 4 0 3 9 3 7 3 9 3 4
 4 6 6 6 4 3 7 5 5 4 9 9 3 8 9 9 4 6 4 0 6 5 9 4 5 5 3 9 8 4 9 4 0 7 5 9 3
 4]


In [49]:
# 把分类结果加入df
df['kmeans'] = labels
df[df.kmeans == 2]

时间                     标题  \
0   2024-09-28 23:34:43         MMD初音未来，UNDEAD   
3   2024-09-25 20:18:35           MMD初音未来，单色骑士   
4   2024-08-10 14:30:53           MMD初音未来，SHOW   
5   2024-08-11 22:54:33            MMD初音未来，卡哇伊   
6   2024-10-13 23:22:15     MMD初音未来，MelticHell   
7   2024-09-01 15:28:21           MMD初音未来，情感风车   
8   2024-08-18 23:20:16            MMD初音未来，RPG   
9   2024-09-14 21:55:59     MMD初音未来，Go-Getters   
10  2024-10-18 23:58:48             MMD初音未来，叭噗   
12  2024-08-13 22:59:23           MMD初音未来，倾诉迷魂   
13  2024-09-20 21:21:34           MMD初音未来，拜拜呀呆   
15  2024-07-28 22:04:25           MMD初音未来，恋爱哲学   
17  2024-07-31 21:43:59       MMD25时，初音未来，心灵烙印   
19  2024-08-24 23:33:03          MMD初音未来，猫尾草之歌   
20  2024-10-12 16:23:07       MMD初音未来，在黎明前一跃而起   
21  2024-09-08 12:28:58      MMD初音未来，甜甜圈洞short   
24  2024-08-28 22:55:49  MMD初音未来，晓山瑞希，宵崎奏，孜然炉火   

                                           URL                     摘要  kmeans  
0   https://www.sohu.com/a/812565548_120122317         MMD初音未来，UNDEAD       2  
3   https://www.sohu.com/a/811660644_120122317           MMD初音未来，单色骑士       2  
4   https://www.sohu.com/a/799888119_120122317           MMD初音未来，SHOW       2  
5   https://www.sohu.com/a/800129858_120122317            MMD初音未来，卡哇伊       2  
6   https://www.sohu.com/a/816244183_120122317     MMD初音未来，MelticHell       2  
7   https://www.sohu.com/a/805468248_120122317           MMD初音未来，情感风车       2  
8   https://www.sohu.com/a/801797229_120122317            MMD初音未来，RPG       2  
9   https://www.sohu.com/a/809054528_120122317     MMD初音未来，Go-Getters       2  
10  https://www.sohu.com/a/817974411_120122317             MMD初音未来，叭噗       2  
12  https://www.sohu.com/a/800642732_120122317           MMD初音未来，倾诉迷魂       2  
13  https://www.sohu.com/a/810397011_120122317           MMD初音未来，拜拜呀呆       2  
15  https://www.sohu.com/a/796798684_120122317           MMD初音未来，恋爱哲学       2  
17  https://www.sohu.com/a/797613538_120122317       MMD25时，初音未来，心灵烙印       2  
19  https://www.sohu.com/a/803409803_120122317          MMD初音未来，猫尾草之歌       2  
20  https://www.sohu.com/a/815933102_120122317       MMD初音未来，在黎明前一跃而起       2  
21  https://www.sohu.com/a/807255356_120122317      MMD初音未来，甜甜圈洞short       2  
24  https://www.sohu.com/a/804480099_120122317  MMD初音未来，晓山瑞希，宵崎奏，孜然炉火       2